In [368]:
import pandas as pd
import numpy as np
import seaborn as sb
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import Lasso
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.preprocessing import MinMaxScaler
from sklearn.compose import TransformedTargetRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, classification_report
from sklearn.preprocessing import LabelBinarizer
import seaborn as sns
from sklearn.feature_extraction.text import CountVectorizer
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import string
import contractions
from num2words import num2words
from textblob import TextBlob
# from spellchecker import SpellChecker
from gensim.models import Word2Vec
import re
# from bs4 import BeautifulSoup
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
# train['SEO Description'] = train['SEO Description'].astype(str)
# train['SEO Description'] = train['SEO Description'].str.lower()

pd.options.display.max_columns = None
pd.options.display.max_rows = None

# Load the dataset
df = pd.read_excel('/users/amulya/Desktop/Tam_2904.xlsx')
df = df.fillna(0)
df.head(1)

[nltk_data] Downloading package punkt to /Users/amulya/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/amulya/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/amulya/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Company                                              Lists  Employees  \
0  Gainsight  Brain 30K SAAS USA, data companies 24, Tarun D...     1300.0   

                            Industry   Company City Company State  \
0  information technology & services  San Francisco    California   

  Company Country                                           Keywords  \
0   United States  enterprise software, saas, predictive analytic...   

                                     SEO Description  \
0  Gainsight's Customer Success and Product Exper...   

                                        Technologies Total Funding  \
0  Salesforce, UltraDns, Sendgrid, Gmail, Mimecas...     156000000   

  Latest Funding Latest Funding Amount       Last Raised At  Annual Revenue  \
0       Series E              52000000  2017-05-09 00:00:00      98000000.0   

   Number of Retail Locations  \
0                         0.0   

                                   Short Description Founded Year  ICP  
0  At Gainsight, our mission is to be living proo...         2009    1

In [369]:
train, test = train_test_split(df,test_size=0.2, random_state=42)
print("Training set size:", len(train))
print("Testing set size:", len(test))
print("set size:", len(df))

Training set size: 3533
Testing set size: 393
set size: 3926


In [370]:
company_backup_test = test['Company'].copy()
company_backup_test.info()

<class 'pandas.core.series.Series'>
Index: 393 entries, 3476 to 2526
Series name: Company
Non-Null Count  Dtype 
--------------  ----- 
393 non-null    object
dtypes: object(1)
memory usage: 6.1+ KB


In [393]:
def pre_process_1(df):
    icp_train_backup = df['ICP'].copy()
    company_train_backup = df['Company'].copy()
    df_dummies = pd.DataFrame({'Employees': df['Employees']})
    # Create binary columns based on employee categories
    df_dummies['emp_lessthan50'] = np.where(df_dummies['Employees'] <= 50, 1, 0)
    df_dummies['emp_50to100'] = np.where((df_dummies['Employees'] > 50) & (df_dummies['Employees'] <= 100), 1, 0)
    df_dummies['emp_100_above'] = np.where(df_dummies['Employees'] > 100, 1, 0)
    df = pd.concat([df, df_dummies], axis=1)  
    df['SEO Description'] = df['SEO Description'].replace(0, 'Others')
    df['SEO Description'] = df['SEO Description'].astype(str)
    df['SEO Description'] = df['SEO Description'].str.lower()
    
    df['SEO Description'] = df['SEO Description'].apply(word_tokenize)
    punctuation = set(string.punctuation)
    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [token for token in tokens if token not in punctuation])

    stop_words = set(stopwords.words('english'))
    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [token for token in tokens if token not in stop_words])

    lemmatizer = WordNetLemmatizer()
    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [lemmatizer.lemmatize(token) for token in tokens])

    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [num2words(token) if token.isdigit() else token for token in tokens])

    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [contractions.fix(token) for token in tokens])

    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [token for token in tokens if token.isalnum()])

    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [token.strip() for token in tokens])

    df['SEO Description'] = df['SEO Description'].apply(lambda tokens: [re.sub(r'http\S+', '', token) for token in tokens])

    df['SEO Description'] = df['SEO Description'].apply(' '.join)
    return df
# train = pre_process_1(train)

In [372]:
def seo_tfidf(df):
    from sklearn.feature_extraction.text import TfidfVectorizer
    import pickle
    from sklearn.preprocessing import LabelBinarizer
    from sklearn.preprocessing import MultiLabelBinarizer
    
    tfidf_vectorizer = TfidfVectorizer()
    tfidf_matrix = tfidf_vectorizer.fit(df['SEO Description'])
    with open('tfidf_vectorizer.pkl', 'wb') as f:
        pickle.dump(tfidf_vectorizer, f)
    ########################
    lb_cities = LabelBinarizer()
    df['Company City'] = df['Company City'].astype(str)
    lb_cities.fit(df['Company City'])
    with open('lb_cities.pkl', 'wb') as f:
        pickle.dump(lb_cities, f) 
    ########################
    df['Technologies'] = df['Technologies'].replace(0, 'Other_technology')
    technologies_lists = df['Technologies'].str.split(',')
    mlb = MultiLabelBinarizer()
    technologies_encoded = mlb.fit(technologies_lists)  
    with open('technologies_encoded.pkl', 'wb') as f:
        pickle.dump(mlb, f)
    ########################
    df['Keywords'] = df['Keywords'].astype(str)
    df['Keywords'] = df['Keywords'].replace(0, 'Other_keyword')
    keywords_lists = df['Keywords'].str.split(',')
    mlb = MultiLabelBinarizer()
    keywords_encoded = mlb.fit(keywords_lists)  
    with open('keywords_encoded.pkl', 'wb') as f:
        pickle.dump(mlb, f) 
    return df

# df = seo_tfidf(df)
# df = seo_process_pickel(df)


In [373]:
def seo_process_pickel(df):
    import pickle
    with open('tfidf_vectorizer.pkl', 'rb') as f:
        loaded_tfidf_vectorizer = pickle.load(f)
    tfidf_matrix = loaded_tfidf_vectorizer.transform(df['SEO Description'])
    feature_names_test = loaded_tfidf_vectorizer.get_feature_names_out()
    seo_done_df = pd.DataFrame(tfidf_matrix.toarray(), columns=feature_names_test)
    df.reset_index(drop=True, inplace=True)
    seo_done_df.reset_index(drop=True, inplace=True)
    df = pd.concat([df, seo_done_df], axis=1)
    ########################
    with open('lb_cities.pkl', 'rb') as f:
        lb_cities = pickle.load(f)
    df['Company City'] = df['Company City'].astype(str)
    cities_proc = lb_cities.transform(df['Company City'])
    cities_df = pd.DataFrame(cities_proc, columns=lb_cities.classes_)
    df.reset_index(drop=True, inplace=True)
    cities_df.reset_index(drop=True, inplace=True)
    df = pd.concat([df, cities_df], axis=1)
    #########################
    with open('technologies_encoded.pkl', 'rb') as f:
        mlb = pickle.load(f)
    df['Technologies'] = df['Technologies'].astype(str)
    technologies_lists = df['Technologies'].str.split(',')
    technologies_encoded = mlb.transform(technologies_lists)
    technologies_encoded_df = pd.DataFrame(technologies_encoded, columns=mlb.classes_)
    df.reset_index(drop=True, inplace=True)
    technologies_encoded_df.reset_index(drop=True, inplace=True)
    df.reset_index(drop=True, inplace=True)
    technologies_encoded_df.reset_index(drop=True, inplace=True)    
    df = pd.concat([df, technologies_encoded_df], axis=1)  
    ###########################
    with open('keywords_encoded.pkl', 'rb') as f:
        mlb = pickle.load(f)
    df['Keywords'] = df['Keywords'].astype(str)
    keywords_lists = df['Keywords'].str.split(',')
    keywords_encoded = mlb.transform(keywords_lists)
    keywords_encoded_df = pd.DataFrame(keywords_encoded, columns=mlb.classes_)
    df.reset_index(drop=True, inplace=True)
    keywords_encoded_df.reset_index(drop=True, inplace=True)

    df.reset_index(drop=True, inplace=True)
    keywords_encoded_df.reset_index(drop=True, inplace=True)
    
    df = pd.concat([df, keywords_encoded_df], axis=1)  
    return df

In [394]:
def drop_columns(df):
    
    df = df.drop(['Company', 'Lists', 'Employees','Company State', 'Company Country', 'SEO Description',
                  'Latest Funding','Industry','Company City','Keywords','Technologies','Last Raised At','Short Description',
                  'Latest Funding Amount','Number of Retail Locations', 'Founded Year','Total Funding','Annual Revenue'], axis = 1)
    # df['ICP'] = df['ICP'].replace({'ICP - 2': 1, 'ICP-1': 1, 'ICP - 1': 1, 'Not an ICP' : 0})
    df['ICP'] = df['ICP'].replace({'S2' : 1, 'S1' : 1, 'S3':1, 'B2' : 1, 'B1' : 1, 'Not Relevant/ Not ICP)': 0,'ICP - 2': 1, 'ICP-1': 1, 'ICP - 1': 1, 'Not an ICP' : 0})

    return df
# df = drop_columns(df)

In [376]:
def all_methods(df):
    train_new = pre_process_1(df)
    train_new = seo_tfidf(train_new)
    train_new = seo_process_pickel(train_new)
    train_new = drop_columns(train_new)
    return train_new
train_final = all_methods(train)

In [377]:
train_final.head(1)

ICP  emp_lessthan50  emp_50to100  emp_100_above  10x  14daydays  160k   1k  \
0    0               0            1              0  0.0        0.0   0.0  0.0   

   1st  20k  21st   2a   2b   2d   2x  30x   3d  3one4  3pl  3sc   3x  4pl  \
0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0    0.0  0.0  0.0  0.0  0.0   

   4tellx  5data   5g   5k  5thkind   5x   8x  a30  a360  a40  aaa  aacsb  \
0     0.0    0.0  0.0  0.0      0.0  0.0  0.0  0.0   0.0  0.0  0.0    0.0   

   aadhaar   ab  abandoned  abandonment  abd  ability  able  abroad  absolute  \
0      0.0  0.0        0.0          0.0  0.0      0.0   0.0     0.0       0.0   

   abstract  abstractor  abundance  academic  academy  accacia  accelarate  \
0       0.0         0.0        0.0       0.0      0.0      0.0         0.0   

   accelerate  accelerated  accelerates  accelerating  acceleration  \
0         0.0          0.0          0.0           0.0           0.0   

   accelerator  accelerist  accelerize  accentiqa  accept  accepted  \
0          0.0         0.0         0.0        0.0     0.0       0.0   

   accepting  access  accessibility  accessible  accessory  accident  accio  \
0        0.0     0.0            0.0         0.0        0.0       0.0    0.0   

   accomplish  accoona  accops  accord  accordingly  account  accountability  \
0         0.0      0.0     0.0     0.0          0.0      0.0             0.0   

   accountable  accountant  accounting  accreditation  accruent  accuracy  \
0          0.0         0.0         0.0            0.0       0.0       0.0   

   accurate  accurately  acd  ace  acesse  ach  achievable  achieve  \
0       0.0         0.0  0.0  0.0     0.0  0.0         0.0      0.0   

   achievement  achieving  achived  acid  acquire  acquisition  across  act  \
0          0.0        0.0      0.0   0.0      0.0          0.0     0.0  0.0   

   acting  action  actionable  activated  activation  active  actively  \
0     0.0     0.0         0.0        0.0         0.0     0.0       0.0   

   activeprospect  activision  activity  actlogica  actor  actual  actum  \
0             0.0         0.0       0.0        0.0    0.0     0.0    0.0   

   acunetix   ad  adapt  adaptable  adaptive  add  added  adding  \
0       0.0  0.0    0.0        0.0       0.0  0.0    0.0     0.0   

   additionally  address  adherence  aditya  adjust  admin  administered  \
0           0.0      0.0        0.0     0.0     0.0    0.0           0.0   

   administration  administrative  admission  adopt  adopting  adoption  adsr  \
0             0.0             0.0        0.0    0.0       0.0       0.0   0.0   

   adtech  advance  advanced  advancement  advancing  advantage  advenio  \
0     0.0      0.0       0.0          0.0        0.0        0.0      0.0   

   adverse  advertisement  advertiser  advertising  advice  advise  \
0      0.0            0.0         0.0          0.0     0.0     0.0   

   advisement  adviser  advisor  advisory  advocacy  advocating  aeromegh  \
0         0.0      0.0      0.0       0.0       0.0         0.0       0.0   

   aerospace  aesthetic  affair  affinity  affordable  africa  age  agen  \
0        0.0        0.0     0.0       0.0         0.0     0.0  0.0   0.0   

   agency  agent  agentless  aggregate  aggregation  aggregator  aggressively  \
0     0.0    0.0        0.0        0.0          0.0         0.0           0.0   

   agile  agility  aging  agnext  agnostic  ago  agreefy  agreement  agri  \
0    0.0      0.0    0.0     0.0       0.0  0.0      0.0        0.0   0.0   

   agribusiness  agriculture  agritech  agvs  ahavaplan  ahead  ahmedabad  \
0           0.0          0.0       0.0   0.0        0.0    0.0        0.0   

    ai  aia  aibuy  aid  aim  aimed  aiming  aiosell  aiproducts  air  \
0  0.0  0.0    0.0  0.0  0.0    0.0     0.0      0.0         0.0  0.0   

   airbrick  airport  airtable  aither  akun  alan  alarm  alert  alertfind  \
0       0.0      0.0       0.0     0.0   0.0   0.0    0.0    0.0        0.0   

   alerti

In [378]:
train_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3533 entries, 0 to 3532
Columns: 19682 entries, ICP to zoho campaigns
dtypes: float64(5766), int64(13916)
memory usage: 530.5 MB


In [395]:
# test = pd.read_excel('/users/amulya/Downloads/9000Austin Dalls - AI_ML Data (1).xlsx')
# # test.rename(columns={'# Employees': 'Employees'}, inplace=True)
# print(test.info())
# test.head(1)
# test['# Employees']
# test['Total Funding'] = test['Total Funding'].fillna(0)

/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:223: UserWarning: Cell N7167 is marked as a date but the serial value 4200000 is outside the limits for dates. The cell will be treated as an error.
  warn(msg)
/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:223: UserWarning: Cell N7174 is marked as a date but the serial value 4594000 is outside the limits for dates. The cell will be treated as an error.
  warn(msg)
/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:223: UserWarning: Cell N7217 is marked as a date but the serial value 13033000 is outside the limits for dates. The cell will be treated as an error.
  warn(msg)
/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:223: UserWarning: Cell N7233 is marked as a date but the serial value 3066000 is outside the limits for dates. The cell 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8968 entries, 0 to 8967
Data columns (total 18 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   Company                     8966 non-null   object 
 1   Lists                       4206 non-null   object 
 2   Employees                   8968 non-null   float64
 3   Industry                    8961 non-null   object 
 4   Company City                8968 non-null   object 
 5   Company State               8965 non-null   object 
 6   Company Country             8968 non-null   object 
 7   Keywords                    4169 non-null   object 
 8   SEO Description             2430 non-null   object 
 9   Technologies                5290 non-null   object 
 10  Total Funding               461 non-null    object 
 11  Latest Funding              499 non-null    object 
 12  Latest Funding Amount       421 non-null    object 
 13  Last Raised At              554 n

Company Lists  Employees  \
0  Southwestern Benefit Designers   NaN        6.0   

                            Industry Company City Company State  \
0  information technology & services       Austin         Texas   

  Company Country Keywords SEO Description Technologies Total Funding  \
0   United States      NaN             NaN          NaN           NaN   

  Latest Funding Latest Funding Amount Last Raised At  Annual Revenue  \
0            NaN                   NaN            NaN             NaN   

   Number of Retail Locations Short Description Founded Year  
0                         NaN               NaN          NaN

In [396]:
def all_methods(df):
    test_new = pre_process_1(df)
    test_new = seo_process_pickel(test_new)
    test_new = drop_columns(test_new)
    return test_new
test_final = all_methods(test)

/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/sklearn/preprocessing/_label.py:900: UserWarning: unknown class(es) [' 2Checkout', ' AdsNative', ' Advanced Solutions International (ASi)', ' Afterpay', ' Aloha POS', ' Altas Relaunched', ' Angular JS v2', ' Arketa', ' Atlas by Facebook', ' AudioEye', ' AvantMetrics', ' Azure Virtual Desktop', ' BigID', ' Blogger', ' BounceExchange', ' Captify', ' Carbon', ' Ceridian', ' Channel Advisor', ' Cision', ' Comm100', ' Complex Media Network', ' Demandforce', ' Demandware', ' Demio', ' Dext', ' DreamHost SSL', ' E-planning', ' EasyDNS', ' Engine Yard', ' F#', ' Fastly CDN', ' Frame.io', ' Google AFS', ' Google GSA', ' Groundtruth', ' Horde', ' HostPapa', ' IfByPhone', ' IgnitionOne', ' InContact', ' Indeed', ' JustUno', ' Kajabi', ' Kaltura', ' LeadLiaison', ' Leadlander', ' Leads by Web.com', ' Lexity', ' LiquidPlanner', ' LivePerson Monitor', ' Loggly', ' Mad Mimi', ' Marchex', ' Media Temple', ' Mindbody', ' Mosyle', ' Mo

In [397]:
print(test_final.info())
test_final.head(1)

# test_final = test_final.drop(['Unnamed: 18','Unnamed: 19','Unnamed: 20','Unnamed: 21','Unnamed: 22','Unnamed: 23','Unnamed: 24','Unnamed: 25','Unnamed: 26','Unnamed: 27','Unnamed: 28','Unnamed: 29','Unnamed: 30'], axis = 1)
# test_final.head(1)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8968 entries, 0 to 8967
Columns: 19681 entries, emp_lessthan50 to zoho campaigns
dtypes: float64(5766), int64(13915)
memory usage: 1.3 GB
None


emp_lessthan50  emp_50to100  emp_100_above  10x  14daydays  160k   1k  1st  \
0               1            0              0  0.0        0.0   0.0  0.0  0.0   

   20k  21st   2a   2b   2d   2x  30x   3d  3one4  3pl  3sc   3x  4pl  4tellx  \
0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0    0.0  0.0  0.0  0.0  0.0     0.0   

   5data   5g   5k  5thkind   5x   8x  a30  a360  a40  aaa  aacsb  aadhaar  \
0    0.0  0.0  0.0      0.0  0.0  0.0  0.0   0.0  0.0  0.0    0.0      0.0   

    ab  abandoned  abandonment  abd  ability  able  abroad  absolute  \
0  0.0        0.0          0.0  0.0      0.0   0.0     0.0       0.0   

   abstract  abstractor  abundance  academic  academy  accacia  accelarate  \
0       0.0         0.0        0.0       0.0      0.0      0.0         0.0   

   accelerate  accelerated  accelerates  accelerating  acceleration  \
0         0.0          0.0          0.0           0.0           0.0   

   accelerator  accelerist  accelerize  accentiqa  accept  accepted  \
0          0.0         0.0         0.0        0.0     0.0       0.0   

   accepting  access  accessibility  accessible  accessory  accident  accio  \
0        0.0     0.0            0.0         0.0        0.0       0.0    0.0   

   accomplish  accoona  accops  accord  accordingly  account  accountability  \
0         0.0      0.0     0.0     0.0          0.0      0.0             0.0   

   accountable  accountant  accounting  accreditation  accruent  accuracy  \
0          0.0         0.0         0.0            0.0       0.0       0.0   

   accurate  accurately  acd  ace  acesse  ach  achievable  achieve  \
0       0.0         0.0  0.0  0.0     0.0  0.0         0.0      0.0   

   achievement  achieving  achived  acid  acquire  acquisition  across  act  \
0          0.0        0.0      0.0   0.0      0.0          0.0     0.0  0.0   

   acting  action  actionable  activated  activation  active  actively  \
0     0.0     0.0         0.0        0.0         0.0     0.0       0.0   

   activeprospect  activision  activity  actlogica  actor  actual  actum  \
0             0.0         0.0       0.0        0.0    0.0     0.0    0.0   

   acunetix   ad  adapt  adaptable  adaptive  add  added  adding  \
0       0.0  0.0    0.0        0.0       0.0  0.0    0.0     0.0   

   additionally  address  adherence  aditya  adjust  admin  administered  \
0           0.0      0.0        0.0     0.0     0.0    0.0           0.0   

   administration  administrative  admission  adopt  adopting  adoption  adsr  \
0             0.0             0.0        0.0    0.0       0.0       0.0   0.0   

   adtech  advance  advanced  advancement  advancing  advantage  advenio  \
0     0.0      0.0       0.0          0.0        0.0        0.0      0.0   

   adverse  advertisement  advertiser  advertising  advice  advise  \
0      0.0            0.0         0.0          0.0     0.0     0.0   

   advisement  adviser  advisor  advisory  advocacy  advocating  aeromegh  \
0         0.0      0.0      0.0       0.0       0.0         0.0       0.0   

   aerospace  aesthetic  affair  affinity  affordable  africa  age  agen  \
0        0.0        0.0     0.0       0.0         0.0     0.0  0.0   0.0   

   agency  agent  agentless  aggregate  aggregation  aggregator  aggressively  \
0     0.0    0.0        0.0        0.0          0.0         0.0           0.0   

   agile  agility  aging  agnext  agnostic  ago  agreefy  agreement  agri  \
0    0.0      0.0    0.0     0.0       0.0  0.0      0.0        0.0   0.0   

   agribusiness  agriculture  agritech  agvs  ahavaplan  ahead  ahmedabad  \
0           0.0          0.0       0.0   0.0        0.0    0.0        0.0   

    ai  aia  aibuy  aid  aim  aimed  aiming  aiosell  aiproducts  air  \
0  0.0  0.0    0.0  0.0  0.0    0.0     0.0      0.0         0.0  0.0   

   airbrick  airport  airtable  aither  akun  alan  alarm  alert  alertfind  \
0       0.0      0.0       0.0     0.0   0.0   0.0    0.0    0.0        0.0   

   alerting  alexa 

In [382]:
train_final.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3533 entries, 0 to 3532
Columns: 19682 entries, ICP to zoho campaigns
dtypes: float64(5766), int64(13916)
memory usage: 530.5 MB


In [398]:
train_columns = set(train_final.columns)
test_columns = set(test_final.columns)

if np.array_equal(train_columns, test_columns):
    print("The feature names are the same for train and test data.")
else:
    print("The feature names are different for train and test data.")

missing_columns_in_test = train_columns - test_columns
print(missing_columns_in_test)

The feature names are different for train and test data.
{'ICP'}


In [384]:
def analysis(y,y_pred):
    train_accuracy = accuracy_score(y, y_pred)
    train_precision = precision_score(y, y_pred)
    train_recall = recall_score(y, y_pred)
    train_f1 = f1_score(y, y_pred)
    print(f'accuracy : {train_accuracy}\nprecision:{train_precision}\nrecall:{train_recall}\nf1_score:{train_f1}')
    return 
    

In [385]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score

y = train_final['ICP']
x = train_final.drop('ICP',axis = 1)

# scaler = MinMaxScaler()
# X_scaled = scaler.fit_transform(x)
# X_scaled = pd.DataFrame(X_scaled, columns = train.columns)
# x_train, x_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.3, random_state=42)
model = LogisticRegression()
model.fit(x, y)
y_pred = model.predict(x)
analysis(y, y_pred)

accuracy : 0.9527313897537504
precision:0.9763513513513513
recall:0.8926640926640926
f1_score:0.9326341266639774


In [386]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score

test_backup_final = test_final['ICP'].copy()

y = test_final['ICP']
x = test_final.drop('ICP',axis = 1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(x)
y_pred_test = model.predict(X_scaled)
# accuracy_test = accuracy_score(y, y_pred_test)
# print('test accuracy:', accuracy_test)
analysis(y, y_pred_test)

accuracy : 0.7455470737913485
precision:0.6985294117647058
recall:0.6168831168831169
f1_score:0.6551724137931034


/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(


In [1]:
# from sklearn.preprocessing import MinMaxScaler
# from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score

# # test_backup_final = test_final['ICP'].copy()
# test_final.columns = test_final.columns.astype(str)
# # y = test_final['ICP']
# x = test_final
# # scaler = MinMaxScaler()
# # X_scaled = scaler.fit_transform(x)
# y_pred_test = model.predict(x)
# print(y_pred_test)
# # test['predicted_output'] = y_pred_test
# # test.head()
# # accuracy_test = accuracy_score(y, y_pred_test)
# # print('test accuracy:', accuracy_test)
# # analysis(y, y_pred_test)

In [387]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score
from sklearn.ensemble import RandomForestClassifier

y = train_final['ICP']
x = train_final.drop('ICP',axis = 1)

scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(x)
RF_model = RandomForestClassifier(criterion = 'log_loss', max_depth= None, min_samples_leaf = 2, min_samples_split = 2, n_estimators = 200)
RF_model.fit(X_scaled, y)
y_pred = RF_model.predict(X_scaled)
analysis(y, y_pred)

accuracy : 0.8683838097933767
precision:0.973744292237443
recall:0.6586872586872586
f1_score:0.7858129894058038


In [388]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score

test_backup_final = test_final['ICP'].copy()

y = test_final['ICP']
x = test_final.drop('ICP',axis = 1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(x)
y_pred_test = RF_model.predict(X_scaled)
analysis(y, y_pred_test)

accuracy : 0.727735368956743
precision:0.7701149425287356
recall:0.43506493506493504
f1_score:0.5560165975103735


In [2]:
# from sklearn.preprocessing import MinMaxScaler
# from sklearn.metrics import precision_score, recall_score, f1_score, confusion_matrix, roc_curve, roc_auc_score

# # test_backup_final = test_final['ICP'].copy()
# test_final.columns = test_final.columns.astype(str)
# # y = test_final['ICP']
# x = test_final
# # scaler = MinMaxScaler()
# # X_scaled = scaler.fit_transform(x)
# y_pred_test = RF_model.predict(x)
# print(y_pred_test)
# test['predicted_output'] = y_pred_test
# test.head()
# accuracy_test = accuracy_score(y, y_pred_test)
# print('test accuracy:', accuracy_test)
# analysis(y, y_pred_test)

In [341]:
from sklearn.naive_bayes import GaussianNB
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = train_final['ICP']
X = train_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)
nb_classifier = GaussianNB()
nb_classifier.fit(X_scaled, y)
y_pred_train = nb_classifier.predict(X_scaled)
analysis(y, y_pred_train)

accuracy : 0.827625247664874
precision:0.6801470588235294
recall:1.0
f1_score:0.8096280087527352


In [342]:
from sklearn.naive_bayes import GaussianNB
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = test_final['ICP']
X = test_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)
y_pred_test = nb_classifier.predict(X_scaled)

analysis(y, y_pred_test)

accuracy : 0.4758269720101781
precision:0.40225563909774437
recall:0.6948051948051948
f1_score:0.5095238095238095


In [389]:
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = train_final['ICP']
X = train_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)
xgb_classifier = xgb.XGBClassifier(colsample_bytree = 0.5,degree = 1, gamma = 2.870346165312448 , kernel= 'poly', learning_rate = 0.01 , max_depth = 10 , n_estimators = 222 ,reg_alpha = 0.19149688983851168, reg_lambda = 0.38837431005558154, subsample = 0.8182619559238651)
xgb_classifier.fit(X_scaled, y)
y_pred_train = xgb_classifier.predict(X_scaled)
analysis(y, y_pred_train)


/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [15:47:23] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "degree", "kernel" } are not used.

  warnings.warn(smsg, UserWarning)


accuracy : 0.838947070478347
precision:0.8903225806451613
recall:0.6393822393822394
f1_score:0.7442696629213483


In [34]:
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from skopt import BayesSearchCV
from skopt.space import Real, Categorical, Integer
y = train_final['ICP']
X = train_final.drop('ICP', axis=1)

# Step 3: Scale the features
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)

param_space = {
    'max_depth': Integer(3, 10),  # Maximum depth of a tree
    'learning_rate': Real(0.01, 1.0, 'log-uniform'),  # Learning rate
    'n_estimators': Integer(100, 1000),  # Number of boosting rounds
    'subsample': Real(0.5, 1.0),  # Subsample ratio of the training instances
    'colsample_bytree': Real(0.5, 1.0),  # Subsample ratio of columns when constructing each tree
    'gamma': Real(0, 5),  # Minimum loss reduction required to make a further partition
    'reg_alpha': Real(0, 1),  # L1 regularization term on weights
    'reg_lambda': Real(0, 1),  # L2 regularization term on weights
    'degree': (1, 6),
    'kernel': ['linear', 'rbf', 'poly']
}
xgb_classifier = xgb.XGBClassifier()

opt = BayesSearchCV(xgb_classifier, param_space, n_iter=50, cv=5, random_state=42)

opt.fit(X_scaled, y)

best_params = opt.best_params_
best_estimator = opt.best_estimator_
# Step 9: Evaluate the best model on the test set
# y_pred_test = best_estimator.predict(X_test_scaled)
# accuracy = accuracy_score(y_test, y_pred_test)
# print("Best Parameters:", best_params)
# print("Test Accuracy:", accuracy)


/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [12:41:44] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "degree", "kernel" } are not used.

  warnings.warn(smsg, UserWarning)
/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [12:41:47] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "degree", "kernel" } are not used.

  warnings.warn(smsg, UserWarning)
/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [12:41:50] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "degree", "kernel" } are not used.

  warnings.warn(smsg, UserWarning)
/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [12:41:52] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "degree", "kern

In [35]:
print(best_estimator)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.5, degree=1, device=None,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=2.870346165312448,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, kernel='poly', learning_rate=0.01,
              max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=10, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=222, n_jobs=None, ...)


In [36]:
print(best_params)

OrderedDict([('colsample_bytree', 0.5), ('degree', 1), ('gamma', 2.870346165312448), ('kernel', 'poly'), ('learning_rate', 0.01), ('max_depth', 10), ('n_estimators', 222), ('reg_alpha', 0.19149688983851168), ('reg_lambda', 0.38837431005558154), ('subsample', 0.8182619559238651)])


In [390]:
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = test_final['ICP']
X = test_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)
y_pred_test = xgb_classifier.predict(X_scaled)
analysis(y, y_pred_test)

accuracy : 0.7557251908396947
precision:0.7636363636363637
recall:0.5454545454545454
f1_score:0.6363636363636364


In [391]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = train_final['ICP']
X = train_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)
adb = AdaBoostClassifier() 
adb.fit(X_scaled,y)
y_pred_train = adb.predict(X_scaled)
analysis(y, y_pred_train)

/opt/homebrew/anaconda3/envs/amulya_base/lib/python3.9/site-packages/sklearn/ensemble/_weight_boosting.py:519: FutureWarning: The SAMME.R algorithm (the default) is deprecated and will be removed in 1.6. Use the SAMME algorithm to circumvent this warning.
  warnings.warn(


accuracy : 0.7679026323238042
precision:0.7303588748787585
recall:0.5814671814671815
f1_score:0.647463456577816


In [392]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = test_final['ICP']
X = test_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_train_scaled = scaler.fit_transform(X)
y_pred_test = adb.predict(X_train_scaled)
analysis(y, y_pred_test)

accuracy : 0.7557251908396947
precision:0.7230769230769231
recall:0.6103896103896104
f1_score:0.6619718309859155


In [347]:
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = train_final['ICP']
X = train_final.drop('ICP', axis=1)
scaler = MinMaxScaler()
X_train_scaled = scaler.fit_transform(X)
svm_model = SVC()
svm_model.fit(X_train_scaled, y)
y_pred_train = svm_model.predict(X_train_scaled)
analysis(y, y_pred_train)

accuracy : 0.9247098782904047
precision:0.9830985915492958
recall:0.8084942084942085
f1_score:0.8872881355932203


In [ ]:
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from skopt import BayesSearchCV
from skopt.space import Real, Categorical, Integer
y = train_final['ICP']
X = train_final.drop('ICP', axis=1)

# Step 3: Scale the features
scaler = MinMaxScaler()
X_scaled = scaler.fit_transform(X)

param_space = {
    # 'C': Real(1e-6, 100.0, 'log-uniform'),    # Regularization parameter
    # 'kernel': Categorical(['linear', 'rbf']),  # Kernel type
    'gamma': Real(1e-6, 10.0, 'log-uniform'),  # Kernel coefficient for 'rbf' and 'poly' kernels
    # 'degree': Integer(1, 6),  
}
svm_classifier = SVC()

opt = BayesSearchCV(svm_classifier, param_space, n_iter=50, cv=5, random_state=42)

opt.fit(X_scaled, y)

best_params = opt.best_params_
best_estimator = opt.best_estimator_

In [348]:
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import accuracy_score
y = test_final['ICP']
X = test_final.drop('ICP', axis=1)
# Scale the features
scaler = MinMaxScaler()
X_test_scaled = scaler.fit_transform(X)

# Predict the labels for test data
y_pred_test = svm_model.predict(X_test_scaled)
analysis(y, y_pred_test)


accuracy : 0.7557251908396947
precision:0.75
recall:0.564935064935065
f1_score:0.6444444444444445


train accuracy - 0.9947368421052631 - when I'm applying grid search cv(C = 100, fit_intercept = False, max_iter = 400, penalty = 'l1', solver = 'liblinear')
test - test accuracy: 0.6421052631578947